# Detect DICOM Image PHI and Redact PHI
- Recommended cluster: >= 15.4 LTS ML (avoid Serverless)

## Setup `pixels` package (if you haven't done so)
1. [Create a git folder](https://docs.databricks.com/aws/en/repos/git-operations-with-repos) cloning the [pixels](https://github.com/databricks-industry-solutions/pixels) package
2. Then run the [`config/setup.py`]($./config/setup) script in the repo folder

In [0]:
%run ./config/setup

Installing Pixels Solution Accelerator dependencies from  /Workspace/Users/yen.low@databricks.com/pixel/pixels
ERROR: pip's dependency resolver does not currently take into account all the packages that are installed. This behaviour is the source of the following dependency conflicts.
petastorm 0.12.1 requires pyspark>=2.1.0, which is not installed.
boto3 1.34.39 requires botocore<1.35.0,>=1.34.39, but you have botocore 1.27.59 which is incompatible.
databricks-feature-engineering 0.8.0 requires mlflow-skinny[databricks]<3,>=2.11.0, but you have mlflow-skinny 3.1.0 which is incompatible.
datasets 2.19.1 requires fsspec[http]<=2024.3.1,>=2023.1.0, but you have fsspec 2022.10.0 which is incompatible.
huggingface-hub 0.27.1 requires fsspec>=2023.5.0, but you have fsspec 2022.10.0 which is incompatible.
jupyter-server 1.23.4 requires anyio<4,>=3.1.0, but you have anyio 4.9.0 which is incompatible.
numba 0.57.1 requires numpy<1.25,>=1.21, but you have numpy 1.26.4 which is incompatible.
s3t

'Done'

In [0]:
%pip install -U pydicom

  Obtaining dependency information for pydicom from https://files.pythonhosted.org/packages/27/a6/98651e752a49f341aa99aa3f6c8ba361728dfc064242884355419df63669/pydicom-3.0.1-py3-none-any.whl.metadata
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 0.0/2.4 MB ? eta -:--:--
   ━━━╸━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 0.2/2.4 MB 6.9 MB/s eta 0:00:01
   ━━━━━━━━━━━╸━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 0.7/2.4 MB 10.1 MB/s eta 0:00:01
   ━━━━━━━━━━━━━━━━━━━━━╺━━━━━━━━━━━━━━━━━━ 1.2/2.4 MB 12.0 MB/s eta 0:00:01
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━╸━━━━━━━ 2.0/2.4 MB 14.2 MB/s eta 0:00:01
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 2.4/2.4 MB 14.3 MB/s eta 0:00:00
  Attempting uninstall: pydicom
    Found existing installation: pydicom 2.4.4
    Uninstalling pydicom-2.4.4:
      Successfully uninstalled pydicom-2.4.4
Note: you may need to restart the kernel using %restart_python or dbutils.library.restartPython() to use updated packages.


In [0]:
import pandas as pd
from dbx.pixels.logging import LoggerProvider

logger = LoggerProvider()

In [0]:
dbutils.widgets.text("table", "hls_radiology.tcia.midi_b_val_subset", label="table of DICOM paths")
table = dbutils.widgets.get("table")
dbutils.widgets.text("output_dir", "/Volumes/hls_radiology/tcia/redacted", label="volumes folder for storing redacted images")
output_dir = dbutils.widgets.get("output_dir")

### Load input dataframe
This assumes a table of DICOM paths already exists with the UC path set in `table`.<br>
To ingest DICOM files into a delta spark table, see [01-dcm-demo]($./01-dcm-demo) for examples.

`VLMPhiExtractor` requires that input be must be ONE of the following:
1. a .dcm file path (e.g. `/Volumes/<catalog>/<schema>/2.1.656.0.2.8048482.9.537.165816238/1-1.dcm`)
2. image file path (e.g. `/Volumes/<catalog>/<schema>/2.1.656.0.2.8048482.9.537.165816238/1-1.jpg`)
3. image encoded as a base64 string required by VLM (e.g. `/9j/4AAQSkZJRgABAQAAAQABAAD/2wBDAAgGBgcGBQgHBwc...`)

In [0]:
df = spark.table(table)
display(df)

SeriesInstanceUID PatientID BodyPartExamined Collection CollectionURI DateReleased FileSize ImageCount Manufacturer ManufacturerModelName Modality ProtocolName SeriesDate SeriesDescription SeriesNumber SoftwareVersions StudyDate StudyDesc StudyInstanceUID ThirdPartyAnalysis TimeStamp PatientID_masked series_id_masked path_masked pixel_hash_masked path series_id pixel_hash frame is_identical jpg_base64str jpg_base64str_masked is_different has_phi 2.1.656.0.2.8048482.9.537.1658163530109825238 1273299863 CHEST MIDI-B-Synthetic-Validation https://doi.org/10.7937/cf2p-aw56 2025-05-02 00:00:00.0 15283394 1 null null DX null 2017-08-11 00:00:00.0 AP 1 1.4 2017-08-11 00:00:00.0 XR CHEST 1 VIEW AP 2.1.656.0.2.8048482.9.537.1460950126025919742 NO 2025-02-23 23:30:04.0 MIDI_1_1_129 1.3.6.1.4.1.14519.5.2.1.8700.9920.153121710989564115753937377722 dbfs:/Volumes/hls_radiology/tcia/downloads/unzipped/1.3.6.1.4.1.14519.5.2.1.8700.9920.153121710989564115753937377722/1-1.dcm 2769535f16e033e3878881a0949b2be16683959e dbfs:/Volumes/hls_radiology/tcia/downloads/unzipped/2.1.656.0.2.8048482.9.537.1658163530109825238/1-1.dcm 2.1.656.0.2.8048482.9.537.1658163530109825238 f1fa359d9c6bdf20019a2cd9a006fd788234164a 1-1 null ... ... true 0 2.4.357.1.0.9259302.8.497.3349013607548370215 1523933739 BREAST MIDI-B-Synthetic-Validation https://doi.org/10.7937/cf2p-aw56 2025-05-02 00:00:00.0 10634156 77 GE MEDICAL SYSTEMS SIGNA EXCITE MR Ordered for Joseph Berry by Dr. Hoover 2014-11-10 00:00:00.0 SAG T2 (FAT-SAT) LEFT for Joseph Berry 20141110 11 2014-11-10 00:00:00.0 MR BREAST, BILATERAL W/WO CONT at HGAWC 2.4.357.1.0.9259302.8.497.2891140086790562459 NO 2025-02-23 23:43:43.0 MIDI_1_1_132 1.3.6.1.4.1.14519.5.2.1.8700.9920.328655332873086989977769633175 dbfs:/Volumes/hls_radiology/tcia/downloads/unzipped/1.3.6.1.4.1.14519.5.2.1.8700.9920.328655332873086989977769633175/1-70.dcm e3e49dadc0a829afac70a5e1e7a7f07f3d9e59b5 dbfs:/Volumes/hls_radiology/tcia/downloads/unzipped/2.4.357.1.0.9259302.8.497.3349013607548370215/1-70.dcm 2.4.357.1.0.9259302.8.497.3349013607548370215 e3e49dadc0a829afac70a5e1e7a7f07f3d9e59b5 1-70 null /9j/4AAQSkZJRgABAQAAAQABAAD/2wBDAAgGBgcGBQgHBwcJCQgKDBQNDAsLDBkSEw8UHRofHh0aHBwgJC4nICIsIxwcKDcpLDAxNDQ0Hyc5PTgyPC4zNDL/wAALCAEAAQABAREA/8QAHwAAAQUBAQEBAQEAAAAAAAAAAAECAwQFBgcICQoL/8QAtRAAAgEDAwIEAwUFBAQAAAF9AQIDAAQRBRIhMUEGE1FhByJxFDKBkaEII0KxwRVS0fAkM2JyggkKFhcYGRolJicoKSo0NTY3ODk6Q0RFRkdISUpTVFVWV1hZWmNkZWZnaGlqc3R1dnd4eXqDhIWGh4iJipKTlJWWl5iZmqKjpKWmp6ipqrKztLW2t7i5usLDxMXGx8jJytLT1NXW19jZ2uHi4+Tl5ufo6erx8vP09fb3+Pn6/9oACAEBAAA/APHjaxKAdgAOCQWOMUiwQLF80Z8w5I5IHXH9KBbIqlyuFIwpzyee1NECBwmz23A8fjSlIlVvlY55B9PrT1t0KnIZjjrngH39qUokbrxuAGOv44FM8kPExBVec9cYHWhYyx2jBIGcjn+dPjRVJHJJ44PQUgbEgYgDPyg54H4UYInLK7EjHBGcntTEIU7SScHtnn/P9KczjGxVBOcqT2FI5CPs5yDjjvS/ffKYLLyRTjH8zMFIXlsg9KbjPH3iR0K/ShMMAGbLDjGRkj0/CkWMKrEtxjC59aXytpChyWxyR2pMGQMZWB5wPWneYjQMeBz2/wA+uaJI1iPzZOeG9jQpZthKgZ5x3PrTiSsh8znuQvAP+eK6vwhCrWd8FEm92XGw7goHU49KNRa3d5fPkEexWXnnc2OMCubYmWMScsSBkEYGcentUGzzO7buvAzk02OMcrkg5x97gH1pT5cilVQLjlufb/61GNyAMcYA3Cm5RT0LKBnk+9SsxEaBjnByVxxik2qsm5cbwM5PQ/X6Z/SmgsM7yCNoJA6E0AFlH8SAFfl9DzQ5O9QAQMBiSOcGkx8+VAyPbkU//VMMZBx83XnnvSYI+bG4ljz1A5/lyKaB9wMDtbpgH1NMfI2/KAR2PWgkgHlmXAxtPT+tO3uJEK4XYcgY5z6GnLFvy4YAq2WBGMc5/wAKTI3sNqHpn6f1pDnIBA8vOQB1FEu9mbAXcO4OefrTl2BcscqMj3X8fSo02kFg2OR1POKUjG3byWHOaeEJyxDLgcEHIOKaWAYkAhc/L78dTTmD4DMqu3XJ7Z7mgIPNILZUDrjOKnYqgGCJHfOQRyPT6cZrsPBdu/8AZ95NEjlA3zeWQCMep9O9V9ai33WPKjZHJb5B/WuYupI3kPlptI5yx+77fWqqvuf5fvE7sA4BNOOFdmIAkOG2DjDZ6f1pUVtzFl3cEjHY+tMjcqq7kznnr1B4xUkg65U5P8I7+hp0rIQQWYMT1656mopCu9mzk8YWlUKqjrnOQfQ0bt7BAGIPB6daJTGpPQquBg+3+TTTukdR823g5x096cxTftByPukHuc00hkZlkBZeij+lKAGJC54YcZx+FBQo7Eu/YcDnHWkwFZg4IAB4Hb0/r+VPIykZ4G4ZO7nmoyQyA4xjtnrj1707AkAIO1x19PakDPGVAbBxzk5GOKDsGQFGRlQc4/yaG2FgkYZVOPmPf2zQUXJz9727kUocqE2kkA5zjP8AkUjSKJF64zyelKEJUt0OCSp7jtTmlIUqvzL/ALXb/OKNjqGJyzEcsOw9fwpQJDcbi2C3zZOMZ6Zr0nwdBDF4TuJpLjEbykMGXBI4+79MVzev3yTXDMx4IGB0HTrx3rn5zloVZUO4Ek564/l0qsoX5h8pYHOB0H1qUHOMY6cFece1RhiqMSBk9dp6Aio4GzFk7izentU+9cxkb

In [0]:
in_df = df.select("path", "has_phi")
in_df = in_df.repartition(8)

## Use Spark ML Pipeline to build a PHI detection and redaction workflow

Build an end-to-end `pyspark.ml.Pipeline` defined with `VLMPhiDetector` and `OcrRedactor` as `Transformer` stages in a workflow. This utilizes Spark ML for highly efficient parallel processing.

1. `VLMPhiDetector` detects and extracts PHI entities using a VLM (set by `endpoint` parameter)
2. `OcrRedactor` masks PHI from images using EasyOCR to detect text boundaries

```
# As a pipeline
Pipeline(stages=[VLMPhiDetector("databricks-claude-3-7-sonnet"), 
                OcrRedactor()])
```

You can also run either stage alone by calling the `transform` method in each class, e.g.

```
detected_df = VLMPhiDetector("databricks-claude-3-7-sonnet").transform(df)
redacted_df = OcrRedactor().transform(df)
```

In [0]:
from dbx.pixels.dicom.dicom_vlm_phi_detector import VLMPhiDetector
from dbx.pixels.dicom.dicom_easyocr_redactor import OcrRedactor

vlm_detector = VLMPhiDetector(endpoint="databricks-claude-3-7-sonnet",
                              inputCol="path", 
                              input_type="dicom")
redactor = OcrRedactor(inputCol="path", outputCol="path_redacted", output_dir=output_dir)

In [0]:
from pyspark.ml import Pipeline
#import mlflow.spark
#mlflow.spark.autolog(disable=True)

processing_pipeline = Pipeline(stages=[vlm_detector, redactor])
processing_model = processing_pipeline.fit(in_df)
out_df = processing_model.transform(in_df)
display(out_df)

🏃 View run bald-wolf-769 at: https://e2-demo-field-eng.cloud.databricks.com/ml/experiments/e149fc8b155f4577ae8fe6934add6537/runs/ddd2d0d591fa49c38acc89c7ffb7da15
🧪 View experiment at: https://e2-demo-field-eng.cloud.databricks.com/ml/experiments/e149fc8b155f4577ae8fe6934add6537


SeriesInstanceUID PatientID BodyPartExamined Collection CollectionURI DateReleased FileSize ImageCount Manufacturer ManufacturerModelName Modality ProtocolName SeriesDate SeriesDescription SeriesNumber SoftwareVersions StudyDate StudyDesc StudyInstanceUID ThirdPartyAnalysis TimeStamp PatientID_masked series_id_masked path_masked pixel_hash_masked path series_id pixel_hash frame is_identical jpg_base64str jpg_base64str_masked is_different has_phi response path_redacted 1.5.566.0.3.5921028.1.523.5821238071079767946 1814567196 CHEST MIDI-B-Synthetic-Validation https://doi.org/10.7937/cf2p-aw56 2025-05-02 00:00:00.0 10735322 1 Philips Medical Systems MobileDiagnost wDR DX Portable Chest 2018-08-05 00:00:00.0 AP 1 2.1 2018-08-05 00:00:00.0 XR CHEST AP PORTABLE 1.5.566.0.3.5921028.1.523.6121491292105488144 NO 2025-02-23 23:40:48.0 MIDI_1_1_026 1.3.6.1.4.1.14519.5.2.1.8700.9920.172433489751933733775728492389 dbfs:/Volumes/hls_radiology/tcia/downloads/unzipped/1.3.6.1.4.1.14519.5.2.1.8700.9920.172433489751933733775728492389/1-1.dcm 38ac7b44eccb22220e12ec91482add9153a7102b dbfs:/Volumes/hls_radiology/tcia/downloads/unzipped/1.5.566.0.3.5921028.1.523.5821238071079767946/1-1.dcm 1.5.566.0.3.5921028.1.523.5821238071079767946 a2b35db9148a36080eb58e0d653e9a15867699c5 1-1 null ... ... true 1 List(List(SANCHEZ TIMOTHY, 08.05.2018, 07.01.1972), 22, 878, 900, null) /Volumes/hls_radiology/tcia/redacted/1.5.566.0.3.5921028.1.523.5821238071079767946_1-1.dcm 1.5.612.0.2.9474539.7.488.8142452478919134598 1867354909 CHEST MIDI-B-Synthetic-Validation https://doi.org/10.7937/cf2p-aw56 2025-05-02 00:00:00.0 15283298 1 null null DX null 2019-02-16 00:00:00.0 AP 1 1.4 2019-02-16 00:00:00.0 XR CHEST 1 VIEW AP 1.5.612.0.2.9474539.7.488.1357077192133292756 NO 2025-02-23 23:30:20.0 MIDI_1_1_028 1.3.6.1.4.1.14519.5.2.1.8700.9920.601124993682414069927085588322 dbfs:/Volumes/hls_radiology/tcia/downloads/unzipped/1.3.6.1.4.1.14519.5.2.1.8700.9920.601124993682414069927085588322/1-1.dcm 277c8d8513e3f5502d70c6aee87ee48a13ddbb84 dbfs:/Volumes/hls_radiology/tcia/downloads/unzipped/1.5.612.0.2.9474539.7.488.8142452478919134598/1-1.dcm 1.5.612.0.2.9474539.7.488.8142452478919134598 5fafbb29ceae3f21ff954c444abaacc948b87260 1-1 null ... ... true 0 List(List(), 6, 794, 800, null) /Volumes/hls_radiology/tcia/redacted/1.5.612.0.2.9474539.7.488.8142452478919134598_1-1.dcm 3.2.435.1.0.5381938.1.237.9592273895273147042 2051580196 CHEST MIDI-B-Synthetic-Validation https://doi.org/10.7937/cf2p-aw56 2025-05-02 00:00:00.0 15896954 2 GE Healthcare WDR1 CR Chest for Anna Robinson 2018-07-12 00:00:00.0 Chest 3808 dm_Gryphon_release-FW10_5A-2014 2018-07-12 00:00:00.0 XR CHEST 2 VIEWS AP OR PA+LAT 3.2.435.1.0.5381938.1.237.5602250777119668442 NO 2025-02-23 23:35:19.0 MIDI_1_1_031 1.3.6.1.4.1.14519.5.2.1.8700.9920.260585602275613172134275061841 dbfs:/Volumes/hls_radiology/tcia/downloads/unzipped/1.3.6.1.4.1.14519.5.2.1.8700.9920.260585602275613172134275061841/1-1.dcm d2ffb7d063469f350a42ace45c17f6ca73753675 dbfs:/Volumes/hls_radiology/tcia/downloads/unzipped/3.2.435.1.0.5381938.1.237.9592273895273147042/1-1.dcm 3.2.435.1.0.5381938.1.237.9592273895273147042 253f8a644e6907075684c35296ee2e37f0f33f64 1-1 null ... ... true 0 List(List(), 6, 906, 912, null) /Volumes/hls_radiology/tcia/redacted/3.2.435.1.0.5381938.1.237.9592273895273147042_1-1.dcm 2.4.167.1.0.5495280.2.998.2172758132580859656 2522288856 COLON MIDI-B-Synthetic-Validation https://doi.org/10.7937/cf2p-aw56 2025-05-02 00:00:00.0 312944152 594 SIEMENS Sensation 64 CT 24ACRIN_Colo at FGH 2019-05-24 00:00:00.0 Colo_supine 1.0 B30f at FGH 20190524 syngo CT 2005A 2019-05-24 00:00:00.0 Abdomen^24ACRIN_Colo (Adult) 20190524 2.4.167.1.0.5495280.2.998.1294095464505661615 NO 2025-02-23 23:43:39.0 MIDI_1_1_139 1.3.6.1.4.1.14519.5.2.1.8700.9920.262461861582733961719828100721 dbfs:/Volumes/hls_radiology/tcia/downloads/unzipped/1.3.6.1.4.1.14519.5.2.1.8700.9920.262461861582733961719828100721/1-527.dcm 7ea38145c826aa7ae5dcbaa493fc4637eb8c354f dbfs

## Evaluate against ground truth

In [0]:
from pyspark.sql.functions import split, col, when, size, isnotnull
import pandas as pd

extracted_df = (out_df
    .withColumn("phi_detected", when(size(col("response.content"))>1, True).otherwise(False))
    .withColumn("redacted", isnotnull(col("path_redacted")))
    .select("has_phi", "phi_detected", "redacted")
)
display(extracted_df)

has_phi phi_detected redacted 1 true true 0 false true 0 false true 0 false false 0 false true 0 false true 0 false true 0 false false 0 false true 0 false false

In [0]:
from dbx.pixels.dicom.dicom_utils import get_classifer_metrics

# Performance of VLMPhiDetector
get_classifer_metrics(extracted_df, col_pred="phi_detected")

{'precision': 1.0,
 'specificity': 1.0,
 'npv': 1.0,
 'recall': 1.0,
 'f1': 1.0,
 'accuracy': 1.0}

In [0]:
# Performance of OcrRedactor
get_classifer_metrics(extracted_df, col_pred="redacted")

{'precision': 0.14285714285714285,
 'specificity': 0.3333333333333333,
 'npv': 1.0,
 'recall': 1.0,
 'f1': 0.25,
 'accuracy': 0.4}

## Add a post-detection filter between `VLMPhiDetector` and `OcrRedactor`
As `OcrRedactor` tends to over-redact, for best performance, we recommend adding a `FilterTransformer` that filters according to the output of `VLMPhiDetector` and is subsequently fed into `OcrRedactor`

In [0]:
from dbx.pixels.dicom.dicom_easyocr_redactor import FilterTransformer

# Use vlm_detector as before
# Add a postdetector filter to nullify the rows without PHI detected by vlm_detector
# Update the redactor to use the filtered column as input instead of the original path
#in_df = spark.table(table)
postdetector_filter = FilterTransformer(inputCol="path", outputCol="filtered")
redactor2 = OcrRedactor(inputCol="filtered",
                       outputCol="path_redacted", 
                       output_dir=output_dir)
dependent_pipeline = Pipeline(stages=[vlm_detector, postdetector_filter, redactor2])
dependent_model = dependent_pipeline.fit(in_df)
out_df_dependent = dependent_model.transform(in_df)
display(out_df_dependent)

🏃 View run awesome-skink-12 at: https://e2-demo-field-eng.cloud.databricks.com/ml/experiments/e149fc8b155f4577ae8fe6934add6537/runs/19941ee6945b422dbbe1510d4f10ac9e
🧪 View experiment at: https://e2-demo-field-eng.cloud.databricks.com/ml/experiments/e149fc8b155f4577ae8fe6934add6537


path has_phi response filtered path_redacted dbfs:/Volumes/hls_radiology/tcia/downloads/unzipped/2.4.167.1.0.5495280.2.998.2172758132580859656/1-527.dcm 0 List(List(), 6, 511, 517, null) null null dbfs:/Volumes/hls_radiology/tcia/downloads/unzipped/1.5.566.0.3.5921028.1.523.5821238071079767946/1-1.dcm 1 List(List(SANCHEZ TIMOTHY, 08.05.2018, 07.01.1972), 22, 878, 900, null) dbfs:/Volumes/hls_radiology/tcia/downloads/unzipped/1.5.566.0.3.5921028.1.523.5821238071079767946/1-1.dcm /Volumes/hls_radiology/tcia/redacted/1.5.566.0.3.5921028.1.523.5821238071079767946_1-1.dcm dbfs:/Volumes/hls_radiology/tcia/downloads/unzipped/3.2.435.1.0.5381938.1.237.9592273895273147042/1-2.dcm 0 List(List(), 6, 962, 968, null) null null dbfs:/Volumes/hls_radiology/tcia/downloads/unzipped/1.5.143.0.1.9349672.6.822.1258491400848416678/1-60.dcm 0 List(List(), 6, 511, 517, null) null null dbfs:/Volumes/hls_radiology/tcia/downloads/unzipped/2.4.357.1.0.9259302.8.497.3349013607548370215/1-70.dcm 0 List(List(), 6, 250, 256, null) null null dbfs:/Volumes/hls_radiology/tcia/downloads/unzipped/2.1.656.0.2.8048482.9.537.1658163530109825238/1-1.dcm 0 List(List(), 6, 794, 800, null) null null dbfs:/Volumes/hls_radiology/tcia/downloads/unzipped/1.5.612.0.2.9474539.7.488.8142452478919134598/1-1.dcm 0 List(List(), 6, 794, 800, null) null null dbfs:/Volumes/hls_radiology/tcia/downloads/unzipped/3.2.435.1.0.5381938.1.237.9592273895273147042/1-1.dcm 0 List(List(), 6, 906, 912, null) null null dbfs:/Volumes/hls_radiology/tcia/downloads/unzipped/1.5.957.1.0.0469346.1.591.1423388835865443258/1-305.dcm 0 List(List(), 6, 511, 517, null) null null dbfs:/Volumes/hls_radiology/tcia/downloads/unzipped/3.1.232.0.0.3150771.5.288.1050421815979028971/1-1.dcm 0 List(List(), 6, 794, 800, null) null null

In [0]:
extracted_df_dependent = (out_df_dependent
    .withColumn("phi_detected", when(size(col("response.content"))>1, True).otherwise(False))
    .withColumn("redacted", isnotnull(col("path_redacted")))
    .select("has_phi", "phi_detected", "redacted")
)
display(extracted_df_dependent)

has_phi phi_detected redacted 0 false false 1 true true 0 false false 0 false false 0 false false 0 false false 0 false false 0 false false 0 false false 0 false false

In [0]:
# Performance of VLMPhiDetector
get_classifer_metrics(extracted_df_dependent, col_pred="phi_detected")

{'precision': 1.0,
 'specificity': 1.0,
 'npv': 1.0,
 'recall': 1.0,
 'f1': 1.0,
 'accuracy': 1.0}

In [0]:
# Performance of OcrRedactor
get_classifer_metrics(extracted_df_dependent, col_pred="redacted")

{'precision': 1.0,
 'specificity': 1.0,
 'npv': 1.0,
 'recall': 1.0,
 'f1': 1.0,
 'accuracy': 1.0}

View the files in the [output_dir](https://e2-demo-field-eng.cloud.databricks.com/explore/data/volumes/hls_radiology/tcia/redacted)